1) Попытаться ответить на вопросы/выдвинуть гипотезы

2) Доделать прошлые домашния задания

3) Прочитать статьи BM25/MatrixFactorization

## Практика:

4) Поэкспериментировать с ALS (grid-search) ********
   * Подобрать лучшие параметры
   * Написать отчет об увиденном

**Ожидание:**
- Отправляем e-mail с топ-10 товарами, отсортированными по вероятности

**Реальность:**
- Чего хочет менеджер от рекомендательной системы? (рост показателя X на Y% за Z недель)
- По-хорошему надо бы предварительно посчитать потенциальный эффект от рекоммендательной системы (Оценки эффектов у менеджера и у вас могут сильно не совпадать: как правило, вы знаете про данные больше)
- А у нас вообще есть e-mail-ы пользователей? Для скольки %? Не устарели ли они?
- Будем ли использовать СМС и push-уведомления в приложении? Может, будем печатать рекомендации на чеке после оплаты на кассе?
- Как будет выглядеть e-mail? (решаем задачу топ-10 рекомендаций или ранжирования? И топ-10 ли?)
- Какие товары должны быть в e-mail? Есть ли какие-то ограничения (только акции и т п)?
- Сколько денег мы готовы потратить на привлечение 1 юзера? CAC - Customer Aquisition Cost. Обычно CAC = расходы на коммуникацию + расходы на скидки
- Cколько мы хотим зарабатывать с одного привлеченного юзера?

**В итоге договорились, что:**
- Хотим повысить выручку минимум на 6% за 4 месяца. Будем повышать за счет роста Retention минимум на  3% и среднего чека минимум на 3%
- Топ-5 товаров, а не топ-10 (В e-mail 10 выглядят не красиво, в push и на чек больше 5 не влезает)
- Рассылаем в e-mail (5% клиентов) и push-уведомлении (20% клиентов), печатаем на чеке (все оффлайн клиенты)
- **3 товара с акцией** (Как это учесть? А если на товар была акция 10%, а потом 50%, что будет стоять в user-item матрице?)
- **1 новый товар** (юзер никогда не покупал. Просто фильтруем аутпут ALS? А если у таких товаров очень маленькая вероятность покупки? Может, использовать другую логику/модель?) 
- **1 товар для роста среднего чека** (товары минимум дороже чем обычно покупает юзер. Как это измерить? На сколько дороже?)

# Ответы
- А точно нужно сортировать по вероятности? Да, так как в пуш уведомлениях скорее всего будет показываться один или пару товаров. Соответственно при сортировки будет показываться наиболее подходящий товар.
- Какую метрику использовать? 
- Сколько раз в неделю отпрпавляем рассылку? Один - два паза в неделю. 
- В какое время отправляем рассылку? Ближе к концу рабочего дня.
- Будем отправлять одному юзеру много раз наши рекоммендации. Как добиться того, чтобы они хоть немного отличались? Добавить акции и скидки. Либо делать рассылку по категориям.
- Нужно ли, чтобы в одной рассылке были *разные* товары? Как определить, что товары *разные*? Как добиться того, чтобы они были разными? Не обязательно разные. Как говорилось выше можно сделать расслку по категориям товаров. "Разные товары" будем считать что это товары из разных категорий. Можно делать рассылку три раза в неделю, где будем отправлять два раза с товарами категории которая наиболее интересна пользователю и один раз "солянку" 

In [3]:
#!pip install implicit==0.4.4

In [7]:
#from google.colab import files

#files.upload()

Saving metrics.py to metrics.py


{'metrics.py': b'"""\nMetrics\n\n"""\nimport numpy as np\n\ndef hit_rate(recommended_list, bought_list):\n    bought_list = np.array(bought_list)\n    recommended_list = np.array(recommended_list)\n    flags = np.isin(bought_list, recommended_list)\n    return (flags.sum() > 0) * 1\n\ndef hit_rate_at_k(recommended_list, bought_list, k=5):\n    return hit_rate(recommended_list[:k], bought_list)\n\ndef precision(recommended_list, bought_list):\n    bought_list = np.array(bought_list)\n    recommended_list = np.array(recommended_list)\n    flags = np.isin(bought_list, recommended_list)\n    return flags.sum() / len(recommended_list)\n\ndef precision_at_k(recommended_list, bought_list, k=5):\n    return precision(recommended_list[:k], bought_list)\n\ndef money_precision_at_k(recommended_list, bought_list, prices_recommended, k=5):\n    recommended_list = np.array(recommended_list)[:k]\n    prices_recommended = np.array(prices_recommended)[:k]\n    flags = np.isin(recommended_list, bought_l

In [9]:
#from google.colab import files

#files.upload()

Saving transaction_data.csv to transaction_data.csv


In [15]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
%matplotlib inline

# Для работы с матрицами
from scipy.sparse import csr_matrix

# Матричная факторизация
from implicit.als import AlternatingLeastSquares
from implicit.nearest_neighbours import bm25_weight, tfidf_weight

# Функции из 1-ого вебинара
import os, sys

module_path = os.path.abspath(os.path.join(os.pardir))
if module_path not in sys.path:
    sys.path.append(module_path)
    
from metrics import precision_at_k, recall_at_k

In [16]:
data = pd.read_csv('transaction_data.csv')

data.columns = [col.lower() for col in data.columns]
data.rename(columns={'household_key': 'user_id',
                    'product_id': 'item_id'},
           inplace=True)


test_size_weeks = 3

data_train = data[data['week_no'] < data['week_no'].max() - test_size_weeks]
data_test = data[data['week_no'] >= data['week_no'].max() - test_size_weeks]

data_train.head(10)

user_id    basket_id  day  item_id  quantity  sales_value  store_id  \
0     2375  26984851472    1  1004906         1         1.39       364   
1     2375  26984851472    1  1033142         1         0.82       364   
2     2375  26984851472    1  1036325         1         0.99       364   
3     2375  26984851472    1  1082185         1         1.21       364   
4     2375  26984851472    1  8160430         1         1.50       364   
5     2375  26984851516    1   826249         2         1.98       364   
6     2375  26984851516    1  1043142         1         1.57       364   
7     2375  26984851516    1  1085983         1         2.99       364   
8     2375  26984851516    1  1102651         1         1.89       364   
9     2375  26984851516    1  6423775         1         2.00       364   

   retail_disc  trans_time  week_no  coupon_disc  coupon_match_disc  
0        -0.60        1631        1          0.0                0.0  
1         0.00        1631        1          0.0                0.0  
2        -0.30        1631        1          0.0                0.0  
3         0.00        1631        1          0.0                0.0  
4        -0.39        1631        1          0.0                0.0  
5        -0.60        1642        1          0.0                0.0  
6        -0.68        1642        1          0.0                0.0  
7        -0.40        1642        1          0.0                0.0  
8         0.00        1642        1          0.0                0.0  
9        -0.79        1642        1          0.0                0.0

In [11]:
#from google.colab import files

#files.upload()

Saving product.csv to product.csv


{'product.csv': b'PRODUCT_ID,MANUFACTURER,DEPARTMENT,BRAND,COMMODITY_DESC,SUB_COMMODITY_DESC,CURR_SIZE_OF_PRODUCT\n25671,2,GROCERY,National,FRZN ICE,ICE - CRUSHED/CUBED,22 LB\n26081,2,MISC. TRANS.,National,NO COMMODITY DESCRIPTION,NO SUBCOMMODITY DESCRIPTION, \n26093,69,PASTRY,Private,BREAD,BREAD:ITALIAN/FRENCH, \n26190,69,GROCERY,Private,FRUIT - SHELF STABLE,APPLE SAUCE,50 OZ\n26355,69,GROCERY,Private,COOKIES/CONES,SPECIALTY COOKIES,14 OZ\n26426,69,GROCERY,Private,SPICES & EXTRACTS,SPICES & SEASONINGS,2.5 OZ\n26540,69,GROCERY,Private,COOKIES/CONES,TRAY PACK/CHOC CHIP COOKIES,16 OZ\n26601,69,DRUG GM,Private,VITAMINS,VITAMIN - MINERALS,300CT(1)\n26636,69,PASTRY,Private,BREAKFAST SWEETS,SW GDS: SW ROLLS/DAN, \n26691,16,GROCERY,Private,PNT BTR/JELLY/JAMS,HONEY,12 OZ\n26738,69,GROCERY,Private,ICE CREAM/MILK/SHERBTS,TRADITIONAL,56 OZ\n26889,32,DRUG GM,National,MAGAZINE,TV/MOVIE-MAGAZINE, \n26941,69,GROCERY,Private,ICE CREAM/MILK/SHERBTS,TRADITIONAL,56 OZ\n27021,2,GROCERY,National,AIR CARE,A

In [3]:
item_features = pd.read_csv('product.csv')
item_features.columns = [col.lower() for col in item_features.columns]
item_features.rename(columns={'product_id': 'item_id'}, inplace=True)

item_features.head(2)

item_id  manufacturer    department     brand            commodity_desc  \
0    25671             2       GROCERY  National                  FRZN ICE   
1    26081             2  MISC. TRANS.  National  NO COMMODITY DESCRIPTION   

            sub_commodity_desc curr_size_of_product  
0          ICE - CRUSHED/CUBED                22 LB  
1  NO SUBCOMMODITY DESCRIPTION

In [4]:
item_features.department.unique()

array(['GROCERY', 'MISC. TRANS.', 'PASTRY', 'DRUG GM', 'MEAT-PCKGD',
       'SEAFOOD-PCKGD', 'PRODUCE', 'NUTRITION', 'DELI', 'COSMETICS',
       'MEAT', 'FLORAL', 'TRAVEL & LEISUR', 'SEAFOOD', 'MISC SALES TRAN',
       'SALAD BAR', 'KIOSK-GAS', 'ELECT &PLUMBING', 'GRO BAKERY',
       'GM MERCH EXP', 'FROZEN GROCERY', 'COUP/STR & MFG', 'SPIRITS',
       'GARDEN CENTER', 'TOYS', 'CHARITABLE CONT', 'RESTAURANT', 'RX',
       'PROD-WHS SALES', 'MEAT-WHSE', 'DAIRY DELI', 'CHEF SHOPPE', 'HBC',
       'DELI/SNACK BAR', 'PORK', 'AUTOMOTIVE', 'VIDEO RENTAL', ' ',
       'CNTRL/STORE SUP', 'HOUSEWARES', 'POSTAL CENTER', 'PHOTO', 'VIDEO',
       'PHARMACY SUPPLY'], dtype=object)

In [5]:
result = data_test.groupby('user_id')['item_id'].unique().reset_index()
result.columns=['user_id', 'actual']
result.head(2)

user_id                                             actual
0        1  [879517, 934369, 1115576, 1124029, 5572301, 65...
1        3  [823704, 834117, 840244, 913785, 917816, 93870...

In [6]:
popularity = data_train.groupby('item_id')['quantity'].sum().reset_index()
popularity.rename(columns={'quantity': 'n_sold'}, inplace=True)

top_5000 = popularity.sort_values('n_sold', ascending=False).head(5000).item_id.tolist()

In [7]:
data_train.loc[~data_train['item_id'].isin(top_5000), 'item_id'] = 999_999

user_item_matrix = pd.pivot_table(data_train, 
                                  index='user_id', columns='item_id', 
                                  values='quantity', 
                                  aggfunc='count', 
                                  fill_value=0
                                 )

user_item_matrix = user_item_matrix.astype(float) 
sparse_user_item = csr_matrix(user_item_matrix)
user_item_matrix.head(3)

/usr/local/lib/python3.7/dist-packages/pandas/core/indexing.py:1817: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self._setitem_single_column(loc, value, pi)


item_id  202291    397896    420647    480014    545926    707683    731106    \
user_id                                                                         
1             0.0       0.0       0.0       0.0       0.0       0.0       0.0   
2             0.0       0.0       0.0       0.0       0.0       0.0       0.0   
3             0.0       0.0       0.0       0.0       0.0       0.0       0.0   

item_id  818980    819063    819227    ...  15926885  15926886  15926887  \
user_id                                ...                                 
1             0.0       0.0       0.0  ...       0.0       0.0       0.0   
2             0.0       0.0       0.0  ...       0.0       0.0       0.0   
3             0.0       0.0       0.0  ...       0.0       0.0       0.0   

item_id  15926927  15927033  15927403  15927661  15927850  16809471  17105257  
user_id                                                                        
1             2.0       0.0       0.0       0.0       0.0       0.0       0.0  
2             1.0       0.0       0.0       0.0       0.0       0.0       0.0  
3             0.0       0.0       0.0       0.0       0.0       0.0       0.0  

[3 rows x 5001 columns]

In [8]:
userids = user_item_matrix.index.values
itemids = user_item_matrix.columns.values

matrix_userids = np.arange(len(userids))
matrix_itemids = np.arange(len(itemids))

id_to_itemid = dict(zip(matrix_itemids, itemids))
id_to_userid = dict(zip(matrix_userids, userids))

itemid_to_id = dict(zip(itemids, matrix_itemids))
userid_to_id = dict(zip(userids, matrix_userids))

In [9]:
def get_recommendations(user, model, N=5):
    res = [id_to_itemid[rec[0]] for rec in 
                    model.recommend(userid=userid_to_id[user], 
                                    user_items=sparse_user_item,   # на вход user-item matrix
                                    N=N, 
                                    filter_already_liked_items=False, 
                                    filter_items=None, 
                                    recalculate_user=True)]
    return res

In [37]:
user_item_matrix_tfidf = tfidf_weight(user_item_matrix.T).T

In [38]:
user_item_matrix_bm25 = bm25_weight(user_item_matrix.T).T 

In [42]:
model = AlternatingLeastSquares(factors=128, 
                                regularization=0.05,
                                iterations=15, 
                                calculate_training_loss=True, 
                                num_threads=4,
                                use_gpu=False)
model.fit(csr_matrix(user_item_matrix_bm25).T.tocsr(),
          show_progress=True)

  0%|          | 0/15 [00:00<?, ?it/s]

In [13]:
%%time
   
result['als_128_0_05'] = result['user_id'].apply(lambda x: get_recommendations(x, model=model, N=5))

result.apply(lambda row: precision_at_k(row['als_128_0_05'], row['actual']), axis=1).mean()

CPU times: user 52.5 s, sys: 39.6 s, total: 1min 32s
Wall time: 52.7 s


In [19]:
result.apply(lambda row: precision_at_k(row['als_32_0_01'], row['actual']), axis=1).mean()

0.1617277749874413

In [20]:
result.apply(lambda row: precision_at_k(row['als_128_0_05'], row['actual']), axis=1).mean()

0.14746358613761748

In [35]:
%%time

result['als_tfidf_128_0_05'] = result['user_id'].apply(lambda x: get_recommendations(x, model=model, N=5))

result.apply(lambda row: precision_at_k(row['als_tfidf_128_0_05'], row['actual']), axis=1).mean()

CPU times: user 52.9 s, sys: 39.5 s, total: 1min 32s
Wall time: 53.5 s


In [33]:
result.apply(lambda row: precision_at_k(row['als_tfidf_32_0_01'], row['actual']), axis=1).mean()

0.16835760924158463

In [36]:
result.apply(lambda row: precision_at_k(row['als_tfidf_128_0_05'], row['actual']), axis=1).mean()

0.15389251632345333

In [43]:
%%time

result['als_bm25_128_0_05'] = result['user_id'].apply(lambda x: get_recommendations(x, model=model, N=5))

result.apply(lambda row: precision_at_k(row['als_bm25_128_0_05'], row['actual']), axis=1).mean()

CPU times: user 52.1 s, sys: 39.6 s, total: 1min 31s
Wall time: 49 s


In [41]:
result.apply(lambda row: precision_at_k(row['als_bm25_32_0_01'], row['actual']), axis=1).mean()

0.1590155700652918

In [44]:
result.apply(lambda row: precision_at_k(row['als_bm25_128_0_05'], row['actual']), axis=1).mean()

0.19266700150677785

Лучшие показатели были у bm25 при factors = 128 и regularization=0.05